# **LAB 02: LÀM VIỆC VÀ TRỰC QUAN HÓA DỮ LIỆU CHUỖI THỜI GIAN**

#### Môn học: Trực quan hóa dữ liệu

#### Nhóm: 5


## **A. Thu thập dữ liệu**




nhóm 5 lựa chọn bộ dữ liệu *U.S. Air Pollution* cho lab 01. Bộ dữ liệu được chia sẻ miễn phí trên nền tảng data.world. (Link dataset: https://data.world/data-society/us-air-pollution-data)

License: <a href="http://opendatacommons.org/licenses/dbcl/1.0/">Database: Open Database, Contents: Database Contents</a>


Bộ dữ liệu được thu thập bằng cách scraped từ database của trang U.S. EPA : https://aqsdr1.epa.gov/aqsweb/aqstmp/airdata/download_files.html


## **B. Khám phá dữ liệu**

### **Import các thư viện**

In [1]:
#!pip install pingouin
#!pip install category_encoders
#!pip install plotly
#!pip install yellowbrick

In [2]:
import pandas as pd
import matplotlib.pyplot as plt
import numpy as np
import seaborn as sns


import warnings
warnings.filterwarnings('ignore')
sns.set_style("whitegrid")
"""
import seaborn as sns
import plotly.express as px
import plotly.offline as py
import matplotlib.pyplot as plt
import numpy as np

import plotly.graph_objs as go
from plotly.subplots import make_subplots
import plotly.figure_factory as ff

import pingouin as pg #for ANOVA

#from sklearn.preprocessing import OneHotEncoder
from sklearn import decomposition
import category_encoders as ce
from sklearn.cluster import KMeans
#from sklearn.metrics import silhouette_score
from scipy.stats import zscore
from yellowbrick.cluster import KElbowVisualizer
"""

%matplotlib inline  

### **Đọc file dữ liệu vào dataframe**

In [3]:
df=pd.read_csv("pollution_us_2000_2016.csv")
df.head()


Unnamed: 0  State Code  County Code  Site Num  \
0           0           4           13      3002   
1           1           4           13      3002   
2           2           4           13      3002   
3           3           4           13      3002   
4           4           4           13      3002   

                                   Address    State    County     City  \
0  1645 E ROOSEVELT ST-CENTRAL PHOENIX STN  Arizona  Maricopa  Phoenix   
1  1645 E ROOSEVELT ST-CENTRAL PHOENIX STN  Arizona  Maricopa  Phoenix   
2  1645 E ROOSEVELT ST-CENTRAL PHOENIX STN  Arizona  Maricopa  Phoenix   
3  1645 E ROOSEVELT ST-CENTRAL PHOENIX STN  Arizona  Maricopa  Phoenix   
4  1645 E ROOSEVELT ST-CENTRAL PHOENIX STN  Arizona  Maricopa  Phoenix   

   Date Local          NO2 Units  ...          SO2 Units  SO2 Mean  \
0  2000-01-01  Parts per billion  ...  Parts per billion  3.000000   
1  2000-01-01  Parts per billion  ...  Parts per billion  3.000000   
2  2000-01-01  Parts per billion  ...  Parts per billion  2.975000   
3  2000-01-01  Parts per billion  ...  Parts per billion  2.975000   
4  2000-01-02  Parts per billion  ...  Parts per billion  1.958333   

   SO2 1st Max Value  SO2 1st Max Hour SO2 AQI           CO Units   CO Mean  \
0                9.0                21    13.0  Parts per million  1.145833   
1                9.0                21    13.0  Parts per million  0.878947   
2                6.6                23     NaN  Parts per million  1.145833   
3                6.6                23     NaN  Parts per million  0.878947   
4                3.0                22     4.0  Parts per million  0.850000   

   CO 1st Max Value  CO 1st Max Hour CO AQI  
0               4.2               21    NaN  
1               2.2               23   25.0  
2               4.2               21    NaN  
3               2.2               23   25.0  
4               1.6               23    NaN  

[5 rows x 29 columns]

### **Tiền xử lý và khám phá dữ liệu**

Đầu tiên ta sẽ xóa cột index của dataset.

In [4]:
df=df.drop(columns="Unnamed: 0")

**Số dòng** và **số cột** của bộ dữ liệu: 1746661 dòng, 28 cột

In [5]:
num_rows, num_cols = df.shape
print("Num rows: ", num_rows)
print("Num cols: ", num_cols)

Num rows:  1746661
Num cols:  28


**Ý nghĩa của mỗi dòng**: Thông tin về nồng độ NO2, O3, SO2, CO trong không khí ở một thành phố trong một ngày.

In [6]:
pd.set_option('display.max_columns', None)
df.head(1)

State Code  County Code  Site Num                                  Address  \
0           4           13      3002  1645 E ROOSEVELT ST-CENTRAL PHOENIX STN   

     State    County     City  Date Local          NO2 Units   NO2 Mean  \
0  Arizona  Maricopa  Phoenix  2000-01-01  Parts per billion  19.041667   

   NO2 1st Max Value  NO2 1st Max Hour  NO2 AQI           O3 Units  O3 Mean  \
0               49.0                19       46  Parts per million   0.0225   

   O3 1st Max Value  O3 1st Max Hour  O3 AQI          SO2 Units  SO2 Mean  \
0              0.04               10      34  Parts per billion       3.0   

   SO2 1st Max Value  SO2 1st Max Hour  SO2 AQI           CO Units   CO Mean  \
0                9.0                21     13.0  Parts per million  1.145833   

   CO 1st Max Value  CO 1st Max Hour  CO AQI  
0               4.2               21     NaN

Kiểm tra xem có dòng nào bị trùng lặp hay không:

In [7]:
df.duplicated().sum()

5032

Thực hiện loại bỏ các dòng trùng lặp:

In [8]:
df=df.drop_duplicates()

**Ý nghĩa của mỗi cột**: 

- `State Code` : Mã tiểu bang.
- `County code` : Mã quận.
- `Site Num` : Số site ở mỗi quận.
- `Address`: Địa chỉ
- `State` : Tên tiểu bang.
- `County` : Tên quận
- `City` : Tên thành phố
- `Date Local` : Ngày thực hiện đo.


4 chất gây ô nhiễm không khí ($NO_2, O_3, SO_2$ và  $O_3$), ứng với mỗi chất có 5 cột giá trị. Ví dụ đối với $NO_2$:

- `NO2 Units` : đơn vị đo lường NO2
- `NO2 Mean` : trung bình nồng độ NO2 trong một ngày cụ thể.
- `NO2 AQI` : chỉ số chất lượng không khí được tính toán bởi NO2 trong một ngày cụ thể.
-   `NO2 1st Max Value` : Giá trị lớn nhất của nồng độ NO2 trong ngày.
- `NO2 1st Max Hour` : Thời gian mà nồng độ NO2 đạt giá trị lớn nhất.

Ta sẽ thực hiện chuẩn hóa tên các cột để thuận tiện hơn cho việc sử dụng về sau:

In [9]:
df.rename(columns=lambda x: x.replace(' ', '_'), inplace=True)

**Kiểu dữ liệu của mỗi cột:**

In [10]:
df.dtypes

State_Code             int64
County_Code            int64
Site_Num               int64
Address               object
State                 object
County                object
City                  object
Date_Local            object
NO2_Units             object
NO2_Mean             float64
NO2_1st_Max_Value    float64
NO2_1st_Max_Hour       int64
NO2_AQI                int64
O3_Units              object
O3_Mean              float64
O3_1st_Max_Value     float64
O3_1st_Max_Hour        int64
O3_AQI                 int64
SO2_Units             object
SO2_Mean             float64
SO2_1st_Max_Value    float64
SO2_1st_Max_Hour       int64
SO2_AQI              float64
CO_Units              object
CO_Mean              float64
CO_1st_Max_Value     float64
CO_1st_Max_Hour        int64
CO_AQI               float64
dtype: object

Cột `Date_Local` chưa có kiểu dữ liệu phù hợp, ta sẽ thực hiện chuyển kiểu dữ liệu về kiểm **datetime**

In [11]:
df['Date_Local'] = pd.to_datetime(df['Date_Local'], format='%Y-%m-%d')

Chuyển các cột `State_Code`, `County_Code` sang **string**

In [12]:
df[['State_Code', 'County_Code']]=df[['State_Code', 'County_Code']].astype(str)

**Kiểm tra giá trị bị thiếu:**

In [13]:
df.isna().sum()/df.shape[0]

State_Code           0.00000
County_Code          0.00000
Site_Num             0.00000
Address              0.00000
State                0.00000
County               0.00000
City                 0.00000
Date_Local           0.00000
NO2_Units            0.00000
NO2_Mean             0.00000
NO2_1st_Max_Value    0.00000
NO2_1st_Max_Hour     0.00000
NO2_AQI              0.00000
O3_Units             0.00000
O3_Mean              0.00000
O3_1st_Max_Value     0.00000
O3_1st_Max_Hour      0.00000
O3_AQI               0.00000
SO2_Units            0.00000
SO2_Mean             0.00000
SO2_1st_Max_Value    0.00000
SO2_1st_Max_Hour     0.00000
SO2_AQI              0.49973
CO_Units             0.00000
CO_Mean              0.00000
CO_1st_Max_Value     0.00000
CO_1st_Max_Hour      0.00000
CO_AQI               0.50010
dtype: float64

Có gần 50% giá trị bị thiếu ở 2 cột `SO2_AQI` và `CO_AQI`

**Phân bố giá trị của các cột numerical:**

Bảng thống kê cơ bản về các phân bố giá trị của các thuộc tính **numeric**:

In [14]:
numeric_cols = df.select_dtypes(include=np.number).columns.tolist()

In [15]:
df[numeric_cols].describe().round(2)

Site_Num    NO2_Mean  NO2_1st_Max_Value  NO2_1st_Max_Hour  \
count  1741629.00  1741629.00         1741629.00        1741629.00   
mean      1120.18       12.82              25.41             11.73   
std       2004.00        9.51              16.00              7.88   
min          1.00       -2.00              -2.00              0.00   
25%          9.00        5.75              13.00              5.00   
50%         60.00       10.74              24.00              9.00   
75%       1039.00       17.71              35.60             20.00   
max       9997.00      139.54             267.00             23.00   

          NO2_AQI     O3_Mean  O3_1st_Max_Value  O3_1st_Max_Hour      O3_AQI  \
count  1741629.00  1741629.00        1741629.00       1741629.00  1741629.00   
mean        23.89        0.03              0.04            10.17       36.04   
std         15.16        0.01              0.02             4.00       19.74   
min          0.00        0.00              0.00             0.00        0.00   
25%         12.00        0.02              0.03             9.00       25.00   
50%         23.00        0.03              0.04            10.00       33.00   
75%         33.00        0.03              0.05            11.00       42.00   
max        132.00        0.10              0.14            23.00      218.00   

         SO2_Mean  SO2_1st_Max_Value  SO2_1st_Max_Hour    SO2_AQI     CO_Mean  \
count  1741629.00         1741629.00        1741629.00  871285.00  1741629.00   
mean         1.87               4.50              9.66       7.12        0.37   
std          2.76               7.69              6.73      11.94        0.31   
min         -2.00              -2.00              0.00       0.00       -0.44   
25%          0.26               0.90              5.00       1.00        0.18   
50%          0.99               2.00              8.00       3.00        0.29   
75%          2.33               5.00             14.00       9.00        0.47   
max        321.62             351.00             23.00     200.00        7.51   

       CO_1st_Max_Value  CO_1st_Max_Hour     CO_AQI  
count        1741629.00       1741629.00  870641.00  
mean               0.62             7.87       6.00  
std                0.64             7.98       5.85  
min               -0.40             0.00       0.00  
25%                0.29             0.00       2.00  
50%                0.40             6.00       5.00  
75%                0.80            13.00       8.00  
max               19.90            23.00     201.00

**Phân bố giá trị của các cột categorical:**

In [16]:
df[set(df.columns)-set(numeric_cols)].describe()

County           City          NO2_Units       State  \
count       1741629        1741629            1741629     1741629   
unique          133            144                  1          47   
top     Los Angeles  Not in a city  Parts per billion  California   
freq          93371         138375            1741629      575628   
first           NaN            NaN                NaN         NaN   
last            NaN            NaN                NaN         NaN   

                 O3_Units           Date_Local County_Code          SO2_Units  \
count             1741629              1741629     1741629            1741629   
unique                  1                 5996          73                  1   
top     Parts per million  2013-04-17 00:00:00          13  Parts per billion   
freq              1741629                  408      149178            1741629   
first                 NaN  2000-01-01 00:00:00         NaN                NaN   
last                  NaN  2016-05-31 00:00:00         NaN                NaN   

                 CO_Units State_Code                 Address  
count             1741629    1741629                 1741629  
unique                  1         47                     204  
top     Parts per million          6  PIKE AVE AT RIVER ROAD  
freq              1741629     575628                   35117  
first                 NaN        NaN                     NaN  
last                  NaN        NaN                     NaN

## **C. Khám phá mối quan hệ trong dữ liệu**

##### **Mối Quan Hệ Giữa Các Thuộc Tính: `NO2_AQI`, `O3_AQI`, `SO2_AQI`, `CO_AQI` theo `Date_Local`**

Trước tiên ta sẽ gom nhóm `NO2_AQI`, `O3_AQI`, `SO2_AQI`, `CO_AQI` theo `Date_Local`. Vì trong một này sẽ có nhiều chỉ số `AQI` nên ta dùng hàm `mean` để tính giá trị đại diện cho ngày hôm đó.

In [17]:
aqi_df = df.groupby(["Date_Local"])[["NO2_AQI", "O3_AQI", "SO2_AQI", "CO_AQI"]].agg(['mean'])
aqi_df = aqi_df.reset_index()
aqi_df.columns = ["Date_Local", "NO2_AQI", "O3_AQI", "SO2_AQI", "CO_AQI"]
aqi_df.head()

Date_Local    NO2_AQI     O3_AQI    SO2_AQI     CO_AQI
0 2000-01-01  32.307692  23.974359  13.384615  16.000000
1 2000-01-02  27.184211  26.973684  11.315789  11.342105
2 2000-01-03  37.233766  19.038961  11.454545  16.131579
3 2000-01-04  38.650000  18.150000  10.125000  18.050000
4 2000-01-05  38.700000  21.675000  11.375000  17.775000

Tiếp theo ta sử dụng biểu đồ đường để trực quan `NO2_AQI`, `O3_AQI`, `SO2_AQI`, `CO_AQI` theo `Date_Local`

In [19]:
import plotly.express as px

fig = px.line(
    aqi_df, 
    x="Date_Local", 
    y=["NO2_AQI", "O3_AQI", "SO2_AQI", "CO_AQI"], 
    labels={
        "Date_Local": "Date Local",
        "value": "AQI"
    }, 
    title="Tên biểu đồ"
)

fig.update_layout(
    legend_title="Pollutants"
)

fig.show()

**Từ biểu đồ ta có vài nhận xét sau:**

- `NO2_AQI`, `O3_AQI` và `CO_AQI` có vẻ có tính chu kỳ theo từng năm, trong khi `SO2_AQI` khá nhiễu.

- Nhìn chung `NO2_AQI`, `O3_AQI`, `SO2_AQI`, `CO_AQI` đều có xu hướng giảm và ổn định hơn qua từng năm.

- Chu kỳ của `NO2_AQI` và `CO_AQI` khá tương đồng nhau khi mà cả 2 cùng chạm đáy và cùng chạm đỉnh.

- Chu kỳ của `O3_AQI` thì ngược lại với chu kỳ của `NO2_AQI` và `CO_AQI`.

Chúng ta sẽ xét kỹ từng thuộc tính để làm rõ hơn những nhận xét trên.

Sử dụng phân tích phân tán chuỗi thời gian (time series decomposition) để phân tích từng thuộc tính và rút ra những nhận xét về Trend, Seasonality và Residuals.

In [20]:
from statsmodels.tsa.seasonal import seasonal_decompose
import plotly.graph_objs as go
from plotly.subplots import make_subplots

pollutants = ["NO2_AQI", "O3_AQI", "SO2_AQI", "CO_AQI"]
colors = ['blue', 'red', 'green', 'orange']

decomposes = [
    seasonal_decompose(aqi_df.set_index("Date_Local")[[pollutant]], model='additive', period=365) 
    for pollutant in pollutants
]

fig_decomposes = []
for i, decompose in enumerate(decomposes):
    fig = make_subplots(rows=3, cols=1, shared_xaxes=True, subplot_titles=('Trend', 'Seasonality', 'Residuals'))

    fig.add_trace(go.Line(x=aqi_df["Date_Local"], y=decompose.trend, line=dict(color=colors[i])), row=1, col=1)
    fig.add_trace(go.Line(x=aqi_df["Date_Local"], y=decompose.seasonal, line=dict(color=colors[i])), row=2, col=1)
    fig.add_trace(go.Line(x=aqi_df["Date_Local"], y=decompose.resid, line=dict(color=colors[i])), row=3, col=1)

    fig.update_layout(title=pollutants[i], showlegend=False)
    fig.update_xaxes(title_text='Date', row=3, col=1)

    fig_decomposes.append(fig)


c:\Users\Acer\anaconda3\lib\site-packages\plotly\graph_objs\_deprecations.py:378: DeprecationWarning:

plotly.graph_objs.Line is deprecated.
Please replace it with one of the following more specific types
  - plotly.graph_objs.scatter.Line
  - plotly.graph_objs.layout.shape.Line
  - etc.




In [21]:
fig_decomposes[0].show()

**NO2_AQI**

- Trend: đang giảm. Điều này cho thấy `NO2_AQI` đang giảm dần theo từng năm.
- Seasonality: ổn định, có biên độ tăng và giảm bằng nhau. Trong một năm, `NO2_AQI` sẽ có 2 lần đạt đỉnh vào các tháng 2, 11 và chạm đáy vào tháng 7
- Residuals: giá trị trung bình xấp xỉ bằng 0 những phương sai lớn và không ổn định. Tuy nhiên, càng về sau thì phương sai có xu hướng nhỏ lại và ổn định hơn.

In [22]:
fig_decomposes[1].show()

**O3_AQI**

- Trend: tăng giảm thất thường. Khó để đưa ra dựa đoán về `O3_AQI` trong tương lai.
- Seasonality: ổn định, có biên độ tăng và giảm bằng nhau. Trong một năm, `O3_AQI` đạt đỉnh vào tháng 6 và có 2 lần chạm đáy vào các tháng 1, 12
- Residuals: giá trị trung bình xấp xỉ bằng 0 những phương sai lớn và không ổn định. Tuy nhiên, càng về sau thì phương sai có xu hướng nhỏ lại và ổn định hơn.

In [23]:
fig_decomposes[2].show()

**SO2_AQI**

- Trend: đang giảm rõ rệt. Điều này cho thấy `SO2_AQI` đang giảm dần theo từng năm.
- Seasonality: hỗn loạn, không có tính thời vụ
- Residuals: giá trị trung bình xấp xỉ bằng 0 những phương sai lớn và không ổn định. Tuy nhiên, càng về sau thì phương sai có xu hướng nhỏ lại và ổn định hơn.

In [24]:
fig_decomposes[3].show()

**CO_AQI**

- Trend: đang giảm rõ rệt. Điều này cho thấy `CO_AQI` đang giảm dần theo từng năm.
- Seasonality: rất ổn định. Trong một năm, `CO_AQI` sẽ có 2 lần đạt đỉnh vào các tháng 1, 12 và chạm đáy vào tháng 7
- Residuals: giá trị trung bình xấp xỉ bằng 0. Phương sai từ năm 2000-2008 lớn và không ổn định nhưng ở giai đoạn sau thì phương sai nhỏ và ổn định hơn một cách rõ rệt.

**Sau khi xét kỹ từng thuộc tính, ta có thể khẳng định các nhận xét lúc đầu là chính xác:**

- `NO2_AQI`, `O3_AQI` và `CO_AQI` có tính chu kỳ theo từng năm, trong khi `SO2_AQI` thì không.

- `NO2_AQI`, `O3_AQI`, `SO2_AQI`, `CO_AQI` đều có xu hướng giảm và ổn định hơn qua từng năm.

- Chu kỳ của `NO2_AQI` và `CO_AQI` tương đồng nhau (cùng đạt đỉnh ở các tháng đầu năm, cuối năm và cùng chạm đáy ở các tháng giữa năm)

- Chu kỳ của `O3_AQI` thì ngược lại với `NO2_AQI` và `CO_AQI` (đạt đỉnh ở các tháng giữa năm và chạm đáy ở các tháng đầu năm, cuối năm)

Tiếp theo ta sẽ sử dụng `correlation coefficient` để đo mức độ tương quan của từng thuộc tính với nhau.

In [25]:
pollutants = ["NO2_AQI", "O3_AQI", "SO2_AQI", "CO_AQI"]
corr = {pol1: [aqi_df[pol1].corr(aqi_df[pol2]) for pol2 in pollutants] for pol1 in pollutants}
corr_df = pd.DataFrame(corr, index=pollutants)
corr_df

NO2_AQI    O3_AQI   SO2_AQI    CO_AQI
NO2_AQI  1.000000 -0.368388  0.671668  0.835466
O3_AQI  -0.368388  1.000000  0.080586 -0.574872
SO2_AQI  0.671668  0.080586  1.000000  0.518070
CO_AQI   0.835466 -0.574872  0.518070  1.000000

In [26]:
heatmap = go.Heatmap(
    z=corr_df.values.tolist(),
    x=corr_df.columns.tolist(),
    y=corr_df.index.tolist(),
    colorscale='Viridis'
)
fig = go.Figure(data=heatmap)
fig.show()


Từ heatmap ta rút ra được một số kết luận sau:

- `NO2_AQI` có tương quan âm với `O3_AQI`. Điều này là hợp lý khi 2 thuộc tính này có chu kỳ ngược nhau, tuy nhiên mối quan hệ giữa `NO2_AQI` và `O3_AQI` chỉ ở mức tạm chấp nhận được khi mà correlation coefficient = -0.37 / -1

- Mặc dù `SO2_AQI` không có chu kỳ theo từng năm như `NO2_AQI` nhưng 2 thuộc tính này lại có quan hệ tương quan dương khá tốt khi mà correlation coefficient = 0.67 / 1

- Trong 4 thuộc tính mà ta xét thì `NO2_AQI` và `CO_AQI` là 2 thuộc tính có quan hệ tương quan mạnh nhất khi mà correlation coefficient = 0.84 / 1. Điều này cũng hợp lý khi mà chu kỳ của 2 thuộc tính này rất giống nhau.

- Cũng trong 4 thuộc tính mà ta xét thì `O3_AQI` và `SO2_AQI` là 2 thuộc tính có quan hệ tương quan yếu nhất, correlation coefficient = 0.08 / 1

- Tương tự như tương quan với `NO2_AQI`; `O3_AQI` có tương quan âm với `CO_AQI` nhưng quan hệ này mạnh hơn khi correlation coefficient = -0.57 / -1

- Tương tự như mối quan hệ giữa `SO2_AQI` và `NO2_AQI`; quan hệ giữa `SO2_AQI` và `CO_AQI` cũng có tương quan dương khá tốt nhưng yếu hơn, correlation coefficient = 0.52 / 1

## **D. Xây dựng mô hình học máy:**

### **1. Chuẩn bị dữ liệu**: 

### **2. Xây dựng mô hình**

### **3. Trực quan hóa mô hình:**

## **E. Tài liệu tham khảo**

https://simerp.io/blog/tim-hieu-nhu-cau-khach-hang/

https://vitalflux.com/pca-explained-variance-concept-python-example/

https://www.datacamp.com/tutorial/decision-tree-classification-python

https://www.kaggle.com/code/utkarshsaxenadn/shop-customer-clustering?fbclid=IwAR29tq6_MlfU848Svyr_Rghg9U3nxiIYaZa3kHgURPZvRh1NwN8Lo8wrkp0